## Querying Twitter API
In this notebook we will use the usernames gained from the previous data analysis, and query Twitter for user data

In [1]:
import os
import re
import datetime as dt
import time
import random
import json

# data science
import math
import numpy as np
import pandas as pd

In [2]:
# configurations

# Allow multiple outputs for each cell
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

# Suppress warnings 
import warnings
warnings.filterwarnings('ignore')

# display all columns
pd.set_option('display.max_columns', None)

# suppress auto-conversion to scientific notation
pd.set_option('display.precision', 6)

# Twitter

In [9]:
import tweepy
import config

Source: https://developer.twitter.com/en/docs/accounts-and-users/follow-search-get-users/api-reference/get-users-lookup
<div>
    <br>
    <img src='Images/lookup.png' style="width:800px">
    <br>
    <img src='Images/lookup2.png' style="width:400px">
</div>

## Obtaining User Access Token
Our user dataset contains 249,844 unique usernames. Under the limit of 300, it would take too long to get all the user data. Obtaining user access token will triple the limit. (See screenshot above)

Source: http://kinocksebastian.blogspot.com/2015/04/how-to-get-access-token-using-tweepy-in.html

In [28]:
# # authenticating twitter consumer key
# auth = tweepy.OAuthHandler(config.consumer_key, config.consumer_secret)
# auth.secure=True
# authUrl = auth.get_authorization_url()

# # go to this url
# print("Please Visit This link and authorize the app ==> " + authUrl)
# print("Enter The Authorization PIN")

In [29]:
# pin = "8470794"

# # set authorization PIN
# token = auth.get_access_token(verifier=pin)

In [30]:
# # write access tokens to file
# accessTokenFile = open("config.py","a")
# accessTokenFile.write(f'user_access_token = "{token[0]}"\n')
# accessTokenFile.write(f'user_access_token_secret = "{token[1]}"\n')
# accessTokenFile.close()

## App Authentication

Switched from app authentication to user authentication to increase the API request limit

In [31]:
# app auth
# auth = tweepy.OAuthHandler(config.consumer_key, config.consumer_secret)
# auth.set_access_token(config.access_token, config.access_token_secret)

# user auth
auth = tweepy.OAuthHandler(config.consumer_key, config.consumer_secret)
auth.set_access_token(config.user_access_token, config.user_access_token_secret)

In [32]:
# Construct the API instance
api = tweepy.API(auth)

## Query Twitter for User Data

In [10]:
users = pd.read_csv('Data/users.csv')

In [33]:
# this function will query Twitter via User/Lookup method 100 users per request, and make 900 requests
# after 900 requests, the function will sleep for 15 minutes as not to exceed the API limit

def queryTwitter(df, start=0, cols):
    end = start + 100
    while True:
        for i in range(899):
            print(f'downloading: {start} ~ {end}')
            
            # query for user objects
            q = df.iloc[start:end]['screenName'].tolist()
            user_objects = api.lookup_users(screen_names=q)
            
            # store all returned user objects in dict; screenName as key and data as value
            users = {user.screen_name:user._json for user in user_objects}
            
            dfx = pd.DataFrame()
            dfx['screenName'] = [name for name in users.keys()]
            for col in cols:
                dfx[col] = [user[col] for user in users.values()]

            with open('Data/user_data.csv', 'a') as f:
                if os.path.isfile('Data/user_data.csv'):
                    dfx.to_csv(f, index=False, header=False)
                else:
                    dfx.to_csv(f, index=False)

            # "If a requested user is unknown, suspended, or deleted [...] not be returned.."
            # see screenshot above
            # note users that weren't found
            notFound = [missing for missing in q if missing not in users.keys()]

            with open('Data/not_found.txt', 'a') as txtfile:
                for i in notFound:
                    txtfile.write(str(i) + '\n')
            
            print('\n'.join([user.screen_name for user in user_objects]), '\n')
            
            start += 100
            if end == len(df):
                print(f'end: {end}')
                return
            if (end + 100) <= len(df):
                end += 100
            elif (end + 100) > len(df):
                end = len(df)
        print(f'Entering sleep: {dt.datetime.now()}\n')
        time.sleep(15 * 60)

In [12]:
len(users)
users.drop_duplicates(inplace=True)
len(users)

241003

241003

In [35]:
cols = ["id_str", "name", "screen_name", "location", "description", "url", "followers_count", 
        "friends_count", "created_at", "favourites_count", "verified", "statuses_count", "lang"]

In [36]:
queryTwitter(users, 0, cols)

---download starting---
downloading: 0 ~ 100
ahmediaTV
DemerisePotvin
TheDawnStott
scottygirl2014
silveriaalison
calrican
traugott_sarah
SchifanoRaelene
BrunusCutis
RDonSteele
_standeliver
european_4
FrancescaBiller
emilyjoypoetry
frozenjo
num1_fan
DougsMom204
page_lie
1mimi4ever
justshocked
ProphetPhella
JessLivMo
collegeclasses5
J_R_Kestner
nvygrl1
GLucivero
IndigoRave
roadgearsun
AliBerlow
SWSupportLV
missremington
rachelndeleon
Meamoore1391
RibaSusan
ChanaDoreaux
BJFrezell
CatherinesIdaho
BekLiza
spikybluealien
cnntoday
javerriaawan
jicReneeMerling
CDNHero
KarenCallesoe
TamDawg79
stcks4
krakmcr
TeeMichelle57
JerusalemFury
downrightdpad
BaptizeFeminism
CCWC_
adelesammarco
NathaliaVasquez
TeutaIllyri
shnikies78
ctlss
Imlooney2M
brooketaggart
wendy08724
icarusfactor
Doris49360681
CamRooMom
iamthatgirl
plainpersin
klkolz
tealraspberry
AnitaSurridge
shinefiercely
emergingW
jandennis1955
BasedAlcatraz
blaiserbeam
savvysuzee
mzelma
4seasonspix
L2MyDaughter
TimCushing
BitchMusic
aaronMCN
A

# Check output

In [5]:
file = open('Data/not_found.txt', 'r', newline='\n')
missing = file.read()
missing = missing.split('\n')

In [6]:
print(f'users not found:{len(missing)}\n')
print('\n'.join(missing))

users not found:106232

JesusPrepper74
ForEverBrenn
dbehan79
VirginiusPrimus
womanontheleft
JC4ever
BRellator
genesis427427
ThalesLives
IE_ANTIFA
Anonfernow
havanaftells
realchrisdantes
CleanGirlSoap
PeterDa22559210
rkeough
ruthayyy
SocialNet_Newz
mysteri00013322
youraposer
sharyalabluff
juno814
darkhorse0102
MiamiBestOf
Benjamin_fredd
LibertarianQn
dirtywater22
ironmanKFF
HunterAwilliam
SuitsGraphics
NewsJunki3
rockykistner1
mellgibsom
NewbieER12
heathermagrath7
ImacatchuS
_LCMB_
lea_majesta
sucks_cnn
HearMyVoice45
SexyJesusX2
emmontoya_
patrick_hilmar
DPSisler
realMichalDinal
ArcJoanof
Berning2020
AutomobilN
morgainmcgovern
PamBiancoUSN
Ignorantconfide
hillbillyspider
CheriRamone
persiStanceinc
FourStarNews
_OffPitch
wbeer
JennyGu_Yingjie
HeSaidThat2
SnapsxxCom
pornhubviid
NeenNeenloom
drays56
AnaPatchouli
renee_papesh
Ronni_see
Twinkle_Towne
DBGrinberg
_Rabble_Rabble
ShelleyResists
mark11_15_
sansanguzman
drewgioh
Andrea8008135
WalkerKorea
CelebNewsFast
DrHarryLyme
TrendStyleDaily
A

In [7]:
missing = pd.DataFrame(missing, columns=['usersNotFound'])

usersNotFound
0         JesusPrepper74
1           ForEverBrenn
2               dbehan79
3        VirginiusPrimus
4         womanontheleft
5                JC4ever
6              BRellator
7          genesis427427
8            ThalesLives
9              IE_ANTIFA
10            Anonfernow
11          havanaftells
12       realchrisdantes
13         CleanGirlSoap
14       PeterDa22559210
15               rkeough
16              ruthayyy
17        SocialNet_Newz
18       mysteri00013322
19            youraposer
20         sharyalabluff
21               juno814
22         darkhorse0102
23           MiamiBestOf
24        Benjamin_fredd
25         LibertarianQn
26          dirtywater22
27            ironmanKFF
28        HunterAwilliam
29         SuitsGraphics
...                  ...
106202           itsTay1
106203         ndgeditor
106204  sargonofakkad100
106205          emocraze
106206           TopRank
106207         NourGoda4
106208       gingerbanks
106209      ericagrieder
106210    timethyisaliar
106211               nfl
106212     jacknapier801
106213     Maxiemcgoober
106214   AnnCoulterDaily
106215   Sargon_of_Akkad
106216         demiEnews
106217      ryanjfelix25
106218            lm3171
106219     marico3850871
106220      BizPacReview
106221          clob9444
106222            phocqu
106223      KimH80593422
106224     blackpanthots
106225     banzetsuatabo
106226   convergingpersp
106227          GSinghPb
106228         EdTheSock
106229      joyellen1962
106230           PenTV26
106231                  

[106232 rows x 1 columns]

In [8]:
len(missing)
missing.dropna(inplace=True)
len(missing)

106232

106232

In [9]:
missing.to_csv('Data/not_found.csv',index=False)

In [13]:
df = pd.read_csv('Data/user_data.csv', encoding='utf-8')
df.head()

screenName              id_str                          name  \
0       ahmediaTV            29976609           Ahmed Tharwat, ثروت   
1  DemerisePotvin  936019403367419909                        DemiP.   
2    TheDawnStott           612216797                    Dawn Stott   
3  scottygirl2014           856719098  Debra - Siren Sword of Truth   
4  silveriaalison  819111315721494528             Go Float Yourself   

      screen_name                        location  \
0       ahmediaTV  https://huzzaz.com/collection/   
1  DemerisePotvin                             NaN   
2    TheDawnStott                         America   
3  scottygirl2014                  Titanic’s Tomb   
4  silveriaalison                Springfield,  OR   

                                         description                      url  \
0  independent TV Host/producer \nhttps://t.co/mi...  https://t.co/JMRyd5shPM   
1                                                NaN                      NaN   
2                               nothing up my sleeve   http://t.co/5FMszbb5yu   
3  Paralegal; Activist/Writer; Investigative Rese...  https://t.co/3QQGxz00F6   
4  VETERAN, Writer, Love is my religion! Living w...  https://t.co/5MrCiBGDCE   

  followers_count friends_count                      created_at  \
0            1084          1031  Thu Apr 09 12:50:17 +0000 2009   
1               1            31  Wed Nov 29 23:49:51 +0000 2017   
2             487          1075  Tue Jun 19 02:59:59 +0000 2012   
3            3410          5002  Mon Oct 01 17:22:33 +0000 2012   
4            1722          1557  Wed Jan 11 09:18:50 +0000 2017   

  favourites_count verified statuses_count lang  
0             1921    False          40471   en  
1               12    False             35   en  
2             7979    False          11848   en  
3           123706    False         103238   en  
4            31516    False          25325   en

In [14]:
len(df)
df.drop_duplicates(inplace=True, subset='screenName', keep='last')
len(df)

87245905

211839

In [15]:
df.reset_index(drop=True, inplace=True)
df.head(20)

screenName              id_str                                 name  \
0       rougbaisers           190672282                               j’aime   
1       CalumSPlath            61073310                       Calum Sherwood   
2         scfuckers  880227723494477829                        Scfuckers.com   
3         shoegal27            20514782                        Karina Thomas   
4   BasedHowardBeal  888919789065973761                        Jeremy Maddux   
5     SANEvents2017           368962215                   Book Sophia Nelson   
6       Cathy_Harri          2392922407                         Cathy Harris   
7         lucycarin            18765167                            lucycarin   
8     christine_w56  782959125076414464  Christine Whybrow:& 𝔶𝔢𝔱, ℑ 𝔭𝔢𝔯𝔰𝔦𝔰𝔱!   
9        HasiNasiBB  919986694597644295                                K. A.   
10           xinemd            26487878                     ❌Les Deplorable❌   
11    Dolce_N_Jeans            27510109                            Paula Mia   
12    140charsordie  877590925685510145                    a tweeted account   
13    charissemarie            15947171                    Charisse Van Horn   
14          Lennonw           111396326                               Lennon   
15          BitSage          1412678124                             Bit Sage   
16   drop_of_indigo           316363225                (((Dame Judi Hench)))   
17          DMLB724            45452890                           Dawn Booth   
18   __TheRightOnee            30986701               B I G   L E X   9/2❄️♍   
19      druz_journo          1962159559                     Rye Druzin ⚡️ 💡📝   

        screen_name                        location  \
0       rougbaisers                    Quelque part   
1       CalumSPlath  London (E17) / Gateshead (NE9)   
2         scfuckers    add my snapchat - DirectPorn   
3         shoegal27                             NaN   
4   BasedHowardBeal                             NaN   
5     SANEvents2017                      Nationwide   
6       Cathy_Harri                             NaN   
7         lucycarin                  Ponca City, OK   
8     christine_w56                             NaN   
9        HasiNasiBB              California, U.S.A.   
10           xinemd                             USA   
11    Dolce_N_Jeans                             USA   
12    140charsordie     West of the Rocky Mountains   
13    charissemarie                    Florida, USA   
14          Lennonw                Washington, D.C.   
15          BitSage                  Washington, DC   
16   drop_of_indigo                     Cardiff, UK   
17          DMLB724          Fort McMurray, Alberta   
18   __TheRightOnee                Stuck in the Mud   
19      druz_journo                 San Antonio, TX   

                                          description  \
0               Je suis ici avec vous, pour l'instant   
1   Sylvia Plath enthusiast. Originally from the N...   
2   visit https://t.co/EYipnQWzZl if you are serio...   
3   B2B marketer and part time #DDMIX instructor w...   
4   Host of The Quiet Place\n\nChaotic Neutral, De...   
5   2018 is here! It's time to Go from your Now to...   
6                   Slightly less curious then a cat.   
7   It isn't braggin if you can do it. I’m a new O...   
8   Electrical Engineer(HONS). Now studying Comp.S...   
9                                                 NaN   
10  #MAGA!! Blocked by CindyMcCain MarthaMcCallum ...   
11  ▶️ Socialite : Steals Pens/Retired Healthcare ...   
12  If you don't vote, you are a loser. If you don...   
13  I write at Celebrity Insider https://t.co/46n3...   
14  Self-proclaimed musical and comedic prodigy, v...   
15  Cyber Security and Technology enthusiast.  Vie...   
16  Upstanding member of the Taffia. Writing ALL T...   
17  Mother. Wife. Editor. Writer. Volunteer. I lov...   
18  The best part of waking up is the alignment of...   
19  @ExpressNews/@HoustonChron e

In [16]:
df.to_csv('Data/users2.csv', index=False, encoding='utf-8')